In [55]:
#Install Dependencies
#!pip3 install torch torchvision torchaudio
#!pip install transformers ipywidgets gradio --upgrade
#!pip install --upgrade gradio
#!pip install nltk
#!pip install jiwer
#!pip install sentencepiece
#!pip install sacremoses
#!pip install soundfile

In [56]:

##translation_pipeline = pipeline('translation_en_to_fr')
##Evaluation Metric = BLEU score
##Exp1
#model_name = "Davlan/byt5-base-eng-yor-mt"
##Exp2
#model_name = "Davlan/m2m100_418M-eng-yor-mt" 
##Exp3
#model_name = "Davlan/mbart50-large-eng-yor-mt"
##Exp4
#model_name = "Davlan/mt5_base_eng_yor_mt"
##Exp5
#model_name = "omoekan/opus-tatoeba-eng-yor"
##Exp6
#model_name = "masakhane/afrimt5_en_yor_news"
##Exp7
#model_name = "masakhane/afrimbart_en_yor_news"
##Exp8
#model_name = "masakhane/afribyt5_en_yor_news"
##Exp9
#model_name = "masakhane/byt5_en_yor_news"
##Exp10
#model_name = "masakhane/mt5_en_yor_news"
#translation_pipeline = pipeline('translation_en_to_yo', model = model_name, max_length=50)

In [57]:
#results = translation_pipeline('My Name is Ayo, I love books')
#results[0]['translation_text']

In [58]:
#results = translation_pipeline('The wages of sin is death')
#results[0]['translation_text']

In [59]:
from transformers import pipeline
import nltk
import jiwer
from nltk.translate.bleu_score import corpus_bleu
from transformers import VitsModel, AutoTokenizer
import torch
import soundfile as sf


WerScore = 0
bleuScore = 0
def translate_transformers(modelName, sourceLangText):
    #results = translation_pipeline(input_text)
    translation_pipeline = pipeline('translation_en_to_yo', model = modelName, max_length=500)
    translated_text = translation_pipeline(sourceLangText) #translator(text)[0]["translation_text"]
    translated_text_target = translated_text[0]['translation_text']
    hypothesis_translations = "My name is Joy, I love reading"
   
    #TTS for the translated_text_target
    #TTS Exp1
    ttsModel = VitsModel.from_pretrained("facebook/mms-tts-yor")
    tokenizer = AutoTokenizer.from_pretrained("facebook/mms-tts-yor")
    ttsInputs = tokenizer(translated_text_target, return_tensors="pt")
   
    with torch.no_grad():
        ttsOutput = ttsModel(**ttsInputs).waveform
    #onvert the tensor to a numpy array
    ttsWaveform = ttsOutput.numpy()[0]    
    #Save the waveform to an audio file
    #sf.write('output.wav', waveform, 22050)
    sf.write('ttsOutput.wav', ttsWaveform, 16000)
    
    #Calculate WerScore
    WerScore = jiwer.wer(translated_text_target, hypothesis_translations)
    #bleuScore = corpus_bleu(translated_text_target,hypothesis_translations)
    
    return translated_text_target,WerScore,'ttsOutput.wav'

In [60]:
#text1 = "Oruko mi ni Ayo, mo feran iwe kika gan"
#text2 = "Agbaninímọ̀ràn kan lórí ọ̀ràn radiation and Clinical Oncologist, tórúkọ rẹ̀ ń jẹ́ Temitope Olatunji-Agunbiade ti kìlọ̀ fáwọn obìnrin pé kí wọ́n má ṣe lo oògùn máàjóyúndúró tàbí kí wọ́n lo oògùn máàjóyúndúró, ó sọ pé ìwádìí ti fi hàn pé lílò tí wọ́n ń lò ó ń mú kí ewu àrùn jẹjẹrẹ ọmú pọ̀ sí i."

#with torch.no_grad():
    #output = ttsModel(**inputs).waveform

In [61]:
#from IPython.display import Audio
#Audio(output, rate=ttsModel.config.sampling_rate)

In [62]:
#Gradio Function and Interface
import gradio as gr
from IPython.display import Audio
interface = gr.Interface(
    fn=translate_transformers,
    inputs=[
        gr.Dropdown(["Davlan/byt5-base-eng-yor-mt", #Exp1
                     "Davlan/m2m100_418M-eng-yor-mt", #Exp2
                     "Davlan/mbart50-large-eng-yor-mt", #Exp3
                     "Davlan/mt5_base_eng_yor_mt", #Exp4
                     "omoekan/opus-tatoeba-eng-yor", #Exp5
                     "masakhane/afrimt5_en_yor_news", #Exp6
                     "masakhane/afrimbart_en_yor_news", #Exp7
                     "masakhane/afribyt5_en_yor_news", #Exp8
                     "masakhane/byt5_en_yor_news", #Exp9
                     "masakhane/mt5_en_yor_news", #Exp10
                     "masakhane/mbart50_en_yor_news", #Exp11
                     "masakhane/m2m100_418M_en_yor_news", #Exp12
                     "masakhane/m2m100_418M_en_yor_rel_news", #Exp13
                     "masakhane/m2m100_418M_en_yor_rel_news_ft", #Exp14
                     "masakhane/m2m100_418M_en_yor_rel", #Exp15
                     #"facebook/nllb-200-distilled-600M", #Exp16
                     #"facebook/nllb-200-3.3B", #Exp17
                     #"facebook/nllb-200-1.3B", #Exp18
                     #"facebook/nllb-200-distilled-1.3B",  #Exp19
                     #"keithhon/nllb-200-3.3B" #Exp20
                     #"CohereForAI/aya-101" #Exp16
                     ], 
                     label="Select Finetuned Eng2Yor Translation Model"),
        gr.Textbox(lines=2, placeholder="Enter English Text Here...", label="English Text")  
    ],
    #outputs = "text",
    #outputs=outputs=["text", "text"],#"text"
    #outputs= gr.Textbox(value="text", label="Translated Text"),
    outputs=[
        gr.Textbox(value="text", label="Translated Yoruba Text"),
        #gr.Textbox(value="text", label=translated_text_actual),
        gr.Textbox(value="number", label="WER(Word Error Rate) Score - The Lower the Better"),
        #gr.Textbox(value="number", label="Bleu Score")
        gr.Audio(type="filepath", label="Click to Generate Yoruba Text2Speech")
    ],
    title="ASPMIR NEURAL MACHINE TRANSLATION(NMT) TESTBED FOR LOW RESOURCED AFRICAN LANGUAGES",
    description="{This Tool Allows Developers and Researchers to Carry Out Experiments on Low Resourced African Languages with State-of-the-Art NMT Finetuned Models.}"
)

interface.launch(share=True)

Running on local URL:  http://127.0.0.1:7879
Running on public URL: https://ccee705195aed67b23.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
